In [1]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

In [2]:
self = DailyPreprocessor()
self.load_data() # 1. 데이터 불러오기
self.make_match1() # 2-1-1
self.make_match2() # 2-1-2
self.make_match3() # 2-1-3
self.make_match4() # 2-1-4
self.make_match5() # 2-1-5

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.


In [3]:
self.turn_type[self.turn_type.node_id=='i8']

node_id    inc_edge_id   out_edge_id turn_type
23      i8  -571500569_01  571500583_02  straight
24      i8  -571500569_01  571500618_01      left
25      i8   571500618_02  571500583_02      left
26      i8   571500618_02  571500617_01  straight
27      i8   571500617_02  571500618_01  straight
28      i8   571500618_02  571500617_01  straight
29      i8   571500617_02  571500618_01  straight
30      i8   571500617_02  571500569_01      left
31      i8   571500583_01  571500617_01      left
32      i8   571500583_01  571500569_01  straight

In [4]:
self.match5 = self.match4.copy()
# 진입진출ID 매칭
for index, row in self.match5.iterrows():
    node_id = self.inter2node[row.inter_no]
    node = self.net.getNode(node_id)
    # 교차로의 모든 (from / to) edges
    inc_edges = [edge for edge in node.getIncoming() if edge.getFunction() == ''] # incoming edges
    out_edges = [edge for edge in node.getOutgoing() if edge.getFunction() == ''] # outgoing edges
    # 교차로의 모든 (from / to) unit vector
    inc_vecs = []
    for inc_edge in inc_edges:
        start = inc_edge.getShape()[-1]
        end = inc_edge.getShape()[-2]
        inc_vec = np.array(end) - np.array(start)
        inc_vec = inc_vec / (inc_vec ** 2).sum() ** 0.5
        inc_vecs.append(inc_vec)
    out_vecs = []
    for out_edge in out_edges:
        start = out_edge.getShape()[0]
        end = out_edge.getShape()[1]
        out_vec = np.array(end) - np.array(start)
        out_vec = out_vec / (out_vec ** 2).sum() ** 0.5
        out_vecs.append(out_vec)
    # 진입각, 진출각 불러오기
    if not pd.isna(row.inc_angle):
        inc_angle = int(row.inc_angle)
        out_angle = int(row.out_angle)
        # 방위각을 일반각으로 가공, 라디안 변환, 단위벡터로 변환
        inc_angle = (90 - inc_angle) % 360
        inc_angle = inc_angle * np.pi / 180.
        inc_vec_true = np.array([np.cos(inc_angle), np.sin(inc_angle)])
        out_angle = (90 - out_angle) % 360
        out_angle = out_angle * np.pi / 180.
        out_vec_true = np.array([np.cos(out_angle), np.sin(out_angle)])
        # 매칭 엣지 반환
        inc_index = np.array([np.dot(inc_vec, inc_vec_true) for inc_vec in inc_vecs]).argmax()
        out_index = np.array([np.dot(out_vec, out_vec_true) for out_vec in out_vecs]).argmax()
        inc_edge_id = inc_edges[inc_index].getID()
        out_edge_id = out_edges[out_index].getID()
        self.match5.at[index, 'inc_edge_id'] = inc_edge_id
        self.match5.at[index, 'out_edge_id'] = out_edge_id
self.match5['node_id'] = self.match5['inter_no'].map(self.inter2node)
self.match5 = self.match5.sort_values(by=['inter_no','phase_no','ring_type']).reset_index(drop=True)

# n2io2turn : dictionary that maps node_id to io2turn
self.n2io2turn = dict()
for node_id in self.parent_ids:
    turn = self.turn_type[self.turn_type.node_id==node_id]
    io = list(zip(turn.inc_edge_id, turn.out_edge_id))
    # io2turn : dictionary that maps (inc_edge_id, out_edge_id) to turn_type
    io2turn = dict(zip(io, turn.turn_type))
    self.n2io2turn[node_id] = io2turn

# turn_type 지정
for i, row in self.match5.iterrows():
    node_id = row.node_id
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    if not (pd.isna(inc_edge_id) and pd.isna(out_edge_id)):
        turn_type = self.n2io2turn[node_id][(inc_edge_id, out_edge_id)]
        self.match5.at[i, 'turn_type'] = turn_type


In [5]:
self = DailyPreprocessor() 
self.load_data() # 1
self.get_matches() # 2
self.initialize_state() # 2-1

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.


1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.


In [6]:
m5 = self.match5[(self.match5.node_id=='i0')]
display(m5)

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   
5       175         3         B        1        동        남       090   
6       175         4         A        5        서        북       270   
7       175         4         B        2        서        동       270   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight  
5       180   571545870_02  571542797_02      i0      left  
6       000   571510153_02  571500487_01      i0      left  
7       090   571510153_02  571545870_01      i0  straight

In [7]:
display(self.match5.head())
display(self.match6.head())
display(self.matching.head())

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight

inter_no node_id  move_no inc_dire out_dire    inc_edge_id   out_edge_id  \
0       175      i0        1        동        남   571545870_02  571542797_02   
1       175      i0        2        서        동   571510153_02  571545870_01   
2       175      i0        3        남        서  -571542797_02  571510153_01   
3       175      i0        4        북        남  -571500487_01  571542797_02   
4       175      i0        5        서        북   571510153_02  571500487_01   

  turn_type  
0      left  
1  straight  
2      left  
3  straight  
4      left

In [8]:
import copy
self = DailyPreprocessor()
self.load_data() # 1. 데이터 불러오기
self.get_matches() # 2-1 매칭테이블 생성
self.initialize_state() # 2-2 신호 초기화

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.


1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.


In [24]:
self.p2PLindices = dict() # parent id to protected left index
for parent_id in self.parent_ids:
    print(parent_id)
    init_state = self.node2init[parent_id]
    # 우회전 이동류 인덱스
    indices_right = [i for i in range(len(init_state)) if init_state[i]=='g']
    # from-to가 지정된 이동류 인덱스
    indices_assigned = []
    m5 = self.match5[(self.match5.node_id==parent_id)].dropna(subset=['inc_edge_id', 'out_edge_id'])
    display(m5)
    for row in m5.itertuples():
        inc_edge = self.net.getEdge(row.inc_edge_id)
        out_edge = self.net.getEdge(row.out_edge_id)
        conns = inc_edge.getConnections(out_edge)
        indices = [conn for conn in conns if conn.getTLLinkIndex()>=0]
        indices = [conn for conn in conns if conn.getJunctionIndex()>=0]
        indices = [conn.getTLLinkIndex() for conn in conns]
        indices_assigned.extend(indices)
    # 좌회전 이동류 인덱스
    indices_left = []
    for row in self.turn_type[self.turn_type.turn_type=='left'].itertuples():
        inc_edge = self.net.getEdge(row.inc_edge_id)
        out_edge = self.net.getEdge(row.out_edge_id)
        conns = inc_edge.getConnections(out_edge)
        indices = [conn for conn in conns if conn.getTLLinkIndex()>=0]
        indices = [conn for conn in conns if conn.getJunctionIndex()>=0]
        indices = [conn.getTLLinkIndex() for conn in conns]
        indices_left.extend(indices)

    PLindices = list((set(range(len(init_state))) - set(indices_right) - set(indices_assigned)).intersection(indices_left))
    self.p2PLindices[parent_id] = PLindices
    print(PLindices)

i0


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0       175         1         A        8        남        북       179   
1       175         1         B        4        북        남       001   
2       175         2         A        7        북        동       001   
3       175         2         B        3        남        서       179   
4       175         3         A        6        동        서       090   
5       175         3         B        1        동        남       090   
6       175         4         A        5        서        북       270   
7       175         4         B        2        서        동       270   

  out_angle    inc_edge_id   out_edge_id node_id turn_type  
0       000  -571542797_02  571500487_01      i0  straight  
1       180  -571500487_01  571542797_02      i0  straight  
2       090  -571500487_01  571545870_01      i0      left  
3       270  -571542797_02  571510153_01      i0      left  
4       270   571545870_02  571510153_01      i0  straight  
5       180   571545870_02  571542797_02      i0      left  
6       000   571510153_02  571500487_01      i0      left  
7       090   571510153_02  571545870_01      i0  straight

[]
i1


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
8        176         1         A        8        남        북       180   
9        176         1         B        4        북        남       359   
10       176         2         A        8        남        북       180   
11       176         2         B        3        남        서       180   
12       176         3         A        5        서        북       270   

   out_angle      inc_edge_id       out_edge_id node_id turn_type  
8        356    -571542810_01  -571542797_02.99      i1  straight  
9        180  571542797_02.99      571542810_01      i1  straight  
10       356    -571542810_01  -571542797_02.99      i1  straight  
11       270    -571542810_01      571543469_01      i1      left  
12       356     571543469_02  -571542797_02.99      i1      left

[]
i2


...

[2]
i8


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
26       201         1         A        8        남        북       180   
27       201         1         B        3        남        서       180   
28       201         2         A        5        서        북       270   
29       201         2         B        2        서        동       270   
30       201         3         A        6        동        서       090   
31       201         3         B        2        서        동       270   
32       201         4         A        6        동        서       090   
33       201         4         B        1        동        남       090   
34       201         5         A        7        북        동       000   
35       201         5         B        4        북        남       000   

   out_angle    inc_edge_id   out_edge_id node_id turn_type  
26       000  -571500569_01  571500583_02      i8  straight  
27       270  -571500569_01  571500618_01      i8      left  
28       000   571500618_02  571500583_02      i8      left  
29       090   571500618_02  571500617_01      i8  straight  
30       270   571500617_02  571500618_01      i8  straight  
31       090   571500618_02  571500617_01      i8  straight  
32       270   571500617_02  571500618_01      i8  straight  
33       180   571500617_02  571500569_01      i8      left  
34       090   571500583_01  571500617_01      i8      left  
35       180   571500583_01  571500569_01      i8  straight

[]
i9


inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
36       202         1         A        6        동        서       090   
37       202         1         B        2        서        동       270   

   out_angle   inc_edge_id      out_edge_id node_id turn_type  
36       270  571510152_02    -571510152_01      i9  straight  
37       090  571510152_01  571510152_01.65      i9  straight

[]


In [10]:
self.match5[(self.match5.node_id=='i2')]

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
14       177         1         A        8        남        북       179   
15       177         1         B        4        북        남       000   
16       177         2         A       17      NaN      NaN       NaN   
17       177         2         B       18      NaN      NaN       NaN   

   out_angle    inc_edge_id   out_edge_id node_id turn_type  
14       000  -571542809_01  571542811_01      i2  straight  
15       180   571542811_02  571542809_01      i2  straight  
16       NaN            NaN           NaN      i2       NaN  
17       NaN            NaN           NaN      i2       NaN

In [11]:
import copy
self = DailyPreprocessor()
self.load_data() # 1. 데이터 불러오기
self.get_matches() # 2-1 매칭테이블 생성
self.initialize_state() # 2-2 신호 초기화
display(self.matching[self.matching.node_id=='i2'])
# matching에 신호 배정
for i, row in self.matching.iterrows():
    node_id = row.node_id
    move_no = row.move_no
    inc_edge = self.net.getEdge(row.inc_edge_id)
    out_edge = self.net.getEdge(row.out_edge_id)
    state = copy.deepcopy(self.node2init[node_id])
    for conn in inc_edge.getConnections(out_edge):
        index = conn.getTLLinkIndex()
        if index >= 0:
            state[index] = 'G'
    self.matching.at[i, 'state'] = ''.join(state)

display(self.matching[self.matching.node_id=='i2'])

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.


inter_no node_id  move_no inc_dire out_dire    inc_edge_id   out_edge_id  \
32       177      i2        1        동        남   571542107_02  571542809_01   
33       177      i2        2        서        동  -571542809_01  571542107_01   
34       177      i2        3        남        서  -571542809_01  571542809_01   
35       177      i2        4        북        남   571542811_02  571542809_01   
36       177      i2        5        서        북  -571542809_01  571542811_01   
37       177      i2        6        동        서   571542107_02  571542809_01   
38       177      i2        7        북        동   571542811_02  571542107_01   
39       177      i2        8        남        북  -571542809_01  571542811_01   
40       177      i2        9       북동       남동   571542107_02  571542809_01   
41       177      i2       10       남서       북동  -571542809_01  571542107_01   
42       177      i2       11       남동       남서  -571542809_01  571542809_01   
43       177      i2       12       북서       남동   571542811_02  571542809_01   
44       177      i2       13       남서       북서  -571542809_01  571542811_01   
45       177      i2       14       북동       남서   571542107_02  571542809_01   
46       177      i2       15       북서       북동   571542811_02  571542107_01   
47       177      i2       16       남동       북서  -571542809_01  571542811_01   

   turn_type  
32      left  
33  straight  
34      left  
35  straight  
36  straight  
37  straight  
38      left  
39  straight  
40      left  
41  straight  
42      left  
43  straight  
44  straight  
45  straight  
46      left  
47  straight

inter_no node_id  move_no inc_dire out_dire    inc_edge_id   out_edge_id  \
32       177      i2        1        동        남   571542107_02  571542809_01   
33       177      i2        2        서        동  -571542809_01  571542107_01   
34       177      i2        3        남        서  -571542809_01  571542809_01   
35       177      i2        4        북        남   571542811_02  571542809_01   
36       177      i2        5        서        북  -571542809_01  571542811_01   
37       177      i2        6        동        서   571542107_02  571542809_01   
38       177      i2        7        북        동   571542811_02  571542107_01   
39       177      i2        8        남        북  -571542809_01  571542811_01   
40       177      i2        9       북동       남동   571542107_02  571542809_01   
41       177      i2       10       남서       북동  -571542809_01  571542107_01   
42       177      i2       11       남동       남서  -571542809_01  571542809_01   
43       177      i2       12       북서       남동   571542811_02  571542809_01   
44       177      i2       13       남서       북서  -571542809_01  571542811_01   
45       177      i2       14       북동       남서   571542107_02  571542809_01   
46       177      i2       15       북서       북동   571542811_02  571542107_01   
47       177      i2       16       남동       북서  -571542809_01  571542811_01   

   turn_type    state  
32      left  rrggrrr  
33  straight  rrgGrrr  
34      left  rrggrrr  
35  straight  GGggrrr  
36  straight  rrggGGG  
37  straight  rrggrrr  
38      left  rrggrrr  
39  straight  rrggGGG  
40      left  rrggrrr  
41  straight  rrgGrrr  
42      left  rrggrrr  
43  straight  GGggrrr  
44  straight  rrggGGG  
45  straight  rrggrrr  
46      left  rrggrrr  
47  straight  rrggGGG

In [12]:
# matching의 각 행을 순회
for row in self.matching.itertuples(index=True):
    node_id = row.node_id
    move_no = row.move_no
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    state = copy.deepcopy(self.node2init)[node_id]

    if move_no != 21:
        inc_edge = self.net.getEdge(inc_edge_id)
        out_edge = self.net.getEdge(out_edge_id)
        for conn in inc_edge.getConnections(out_edge):
            index = conn.getTLLinkIndex()
            if index >= 0:
                state[index] = 'G'
        self.matching.at[row.Index, 'state'] = ''.join(state)

self.matching = self.matching.dropna(subset='state')
self.matching = self.matching.reset_index(drop=True)
self.matching = self.matching[['inter_no', 'node_id', 'move_no', 'inc_edge_id', 'out_edge_id', 'state']]

In [13]:
display(self.match6)
self.assign_signals() # 2-3 신호배정
display(self.match6)

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0         175         1         A        8        남        북       179   
1         175         1         B        4        북        남       001   
2         175         2         A        7        북        동       001   
3         175         2         B        3        남        서       179   
4         175         3         A        6        동        서       090   
..        ...       ...       ...      ...      ...      ...       ...   
103       210         2         B        2        서        동       270   
104       210         3         A        7        북        동       000   
105       210         3         B        4        북        남       000   
106       210         4         A        8        남        북       180   
107       210         4         B        3        남        서       180   

    out_angle    inc_edge_id   out_edge_id node_id turn_type  
0         000  -571542797_02  571500487_01      i0  straight  
1         180  -571500487_01  571542797_02      i0  straight  
2         090  -571500487_01  571545870_01      i0      left  
3         270  -571542797_02  571510153_01      i0      left  
4         270   571545870_02  571510153_01      i0  straight  
..        ...            ...           ...     ...       ...  
103       090            NaN           NaN     u60  straight  
104       090            NaN           NaN     u60      left  
105       180            NaN           NaN     u60  straight  
106       000            NaN           NaN     u60  straight  
107       270            NaN           NaN     u60      left  

[108 rows x 12 columns]

2-3. 직진 및 좌회전(G)을 배정했습니다.


inter_no node_id  phase_no ring_type  move_no    inc_edge_id  \
0         175      i0         1         A        8  -571542797_02   
1         175      i0         1         B        4  -571500487_01   
2         175      i0         2         A        7  -571500487_01   
3         175      i0         2         B        3  -571542797_02   
4         175      i0         3         A        6   571545870_02   
..        ...     ...       ...       ...      ...            ...   
103       210     u60         2         B        2            NaN   
104       210     u60         3         A        7            NaN   
105       210     u60         3         B        4            NaN   
106       210     u60         4         A        8            NaN   
107       210     u60         4         B        3            NaN   

      out_edge_id              state  
0    571500487_01  grrrgrrrgGGGGrgrr  
1    571542797_02  gGGrgrrrgrrrrrgrr  
2    571545870_01  grrGgrrrgrrrrrgrr  
3    571510153_01  grrrgrrrgrrrrGgrr  
4    571510153_01  grrrgGGrgrrrrrgrr  
..            ...                ...  
103           NaN          GGGGGGGGr  
104           NaN          GGGGGGGGr  
105           NaN          GGGGGGGGr  
106           NaN          GGGGGGGGr  
107           NaN          GGGGGGGGr  

[108 rows x 8 columns]